# Exploring BETA

This notebook is used to generate the datasets to explore the new metric beta.

In [4]:
%load_ext autoreload
%autoreload 2

In [6]:
import os
import sys
from pathlib import Path
import json

import numpy as np
import pandas as pd
from IPython.display import display, Markdown, Latex

home = str(Path.home())

RPLIB_DATA_PREFIX = os.environ.get("RPLIB_DATA_PREFIX")

if RPLIB_DATA_PREFIX is None: # Set default
    RPLIB_DATA_PREFIX=f'{home}/RPLib/data'
    
try:
    import pyrankability as pyrankability
    import pyrplib as pyrplib
except:
    print('Looking for packages in home directory')
    sys.path.insert(0,f"{home}") # Add the home directory relevant paths to the PYTHONPATH
    sys.path.insert(0,f"{home}/ranking_toolbox") # Add the home directory relevant paths to the PYTHONPATH
    sys.path.insert(0,f"{home}/RPLib") # Add the home directory relevant paths to the PYTHONPATH
    import pyrankability
    import pyrplib

import pandas as pd

from pyrplib.artificial import *

## Create datasets

In [7]:
rplib_data = pyrplib.data.Data(RPLIB_DATA_PREFIX)

### Create an artificial dataset

In [ ]:
from datetime import datetime
thresholds = [1,2,3,4,5]
num_games = 1000

np.random.seed(0)

datasets = {}
for threshold in thresholds:
    options = {
        "number_matrices":30,
        "number_of_rows_columns": 20,
        "threshold":threshold,
        "num_games":1000
    }
    dataset = create_dataset(pyrplib.artificial.example_create,options)
    #dataset = create_dataset(pyrplib.artificial.example_create3,pyrplib.artificial.example_get_create_options3())
    datasets[threshold] = dataset
    dataset.to_json(f'../beta_structured_artificial/threshold_dataset_{threshold}.json')

In [9]:
cards = {}
for threshold in thresholds:
    cards[threshold] = {}
    for index in datasets[threshold].Ds.index:
        D = datasets[threshold].Ds.loc[index]
        cards[threshold][index] = pyrplib.card.LOP().prepare(pyrplib.transformers.process_D(D)).run()

Academic license - for non-commercial use only - expires 2022-09-05
Using license file /home/jupyter-pander14/gurobi.lic
Cannot find multiple solutions (or another problem occured)
Cannot find multiple solutions (or another problem occured)
Cannot find multiple solutions (or another problem occured)
Cannot find multiple solutions (or another problem occured)
Cannot find multiple solutions (or another problem occured)
Cannot find multiple solutions (or another problem occured)
Cannot find multiple solutions (or another problem occured)
Cannot find multiple solutions (or another problem occured)


In [15]:
info_df = pd.DataFrame(columns=["Threshold",'index','obj','beta','tau','nmos']).set_index(["Threshold",'index'])
for threshold in thresholds:
    for index in datasets[threshold].Ds.index:
        card = cards[threshold][index]
        info_df.loc[(threshold,index),'obj'] = card.obj
        info_df.loc[(threshold,index),'beta'] = card.beta    
        info_df.loc[(threshold,index),'nmos'] = len(card.solutions)
        info_df.loc[(threshold,index),'tau'] = card.tau_farthest_pair
info_df = info_df.infer_objects()
info_df = info_df.reset_index()

In [16]:
info_df

Threshold  index    obj          beta       tau  nmos
0            1      0  966.0  4.703337e-07  0.989474     2
1            1      1  970.0  1.760020e-06  0.968421     6
2            1      2  966.0  2.546293e-05  0.894737    36
3            1      3  965.0  2.047631e-06  0.968421     6
4            1      4  964.0  8.377800e-06  0.915789    32
..         ...    ...    ...           ...       ...   ...
145          5     25  816.0  1.295456e-04  0.842105    27
146          5     26  817.0  7.620779e-06  0.926316     8
147          5     27  815.0  3.133357e-06  0.968421     8
148          5     28  835.0  0.000000e+00       NaN     1
149          5     29  815.0  1.459317e-04  0.789474    12

[150 rows x 6 columns]

In [17]:
info_df.drop(columns=['index']).corr()

Threshold       obj      beta       tau      nmos
Threshold   1.000000 -0.988424  0.489958 -0.521089  0.179559
obj        -0.988424  1.000000 -0.504006  0.529071 -0.199039
beta        0.489958 -0.504006  1.000000 -0.808384  0.364954
tau        -0.521089  0.529071 -0.808384  1.000000 -0.588123
nmos        0.179559 -0.199039  0.364954 -0.588123  1.000000

### Creating D matrices with multiple optimal solutions

In [18]:
D = pyrplib.artificial.domplusnoise(20,0)
D2 = addmossimple(D,0,4)
D3 = addmossimple(D,5,9)
D4 = addmossimple(D,10,14)
D5 = addmossimple(D,15,19)

In [19]:
manual_dataset = pyrplib.artificial.create_dataset_manual([D,D2,D3,D4,D5],
                                         {
                                             "start_index":[None,0,5,10,15],
                                             "end_index":[None,4,9,14,19]
                                         },
                                         create_code='addmossimple(D_matrics[0],start_index[i],start_index[i])]')

In [20]:
dataset.to_json("../beta_structured_artificial/manual_dataset.json")

In [109]:
lop_card = pyrplib.card.LOP().prepare(pyrplib.transformers.process_D(D))
lop_card.run()

Cannot find multiple solutions (or another problem occured)


In [47]:
D2

0   1   2   3   4   5   6   7   8   9   10  11  12  13  14  15  16  17  \
0    0   1   1   1   1   1   1   1   1   1   1   1   1   1   1   1   1   1   
1    1   0   1   1   1   1   1   1   1   1   1   1   1   1   1   1   1   1   
2    1   1   0   1   1   1   1   1   1   1   1   1   1   1   1   1   1   1   
3    1   1   1   0   1   1   1   1   1   1   1   1   1   1   1   1   1   1   
4    1   1   1   1   0   1   1   1   1   1   1   1   1   1   1   1   1   1   
5    0   0   0   0   0   0   1   1   1   1   1   1   1   1   1   1   1   1   
6    0   0   0   0   0   0   0   1   1   1   1   1   1   1   1   1   1   1   
7    0   0   0   0   0   0   0   0   1   1   1   1   1   1   1   1   1   1   
8    0   0   0   0   0   0   0   0   0   1   1   1   1   1   1   1   1   1   
9    0   0   0   0   0   0   0   0   0   0   1   1   1   1   1   1   1   1   
10   0   0   0   0   0   0   0   0   0   0   0   1   1   1   1   1   1   1   
11   0   0   0   0   0   0   0   0   0   0   0   0   1   1   1   1   1   1   
12   0   0   0   0   0   0   0   0   0   0   0   0   0   1   1   1   1   1   
13   0   0   0   0   0   0   0   0   0   0   0   0   0   0   1   1   1   1   
14   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   1   1   1   
15   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   1   1   
16   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   1   
17   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   
18   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   
19   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   

    18  19  
0    1   1  
1    1   1  
2    1   1  
3    1   1  
4    1   1  
5    1   1  
6    1   1  
7    1   1  
8    1   1  
9    1   1  
10   1   1  
11   1   1  
12   1   1  
13   1   1  
14   1   1  
15   1   1  
16   1   1  
17   1   1  
18   0   1  
19   0   0

In [117]:
lop_card2 = pyrplib.card.LOP().prepare(pyrplib.transformers.process_D(D2))
lop_card2.run()

Found multiple solutions


/home/jupyter-pander14/ranking_toolbox/pyrankability/search.py:740: ParserWarning: Falling back to the 'python' engine because the 'c' engine does not support regex separators (separators > 1 char and different from '\s+' are interpreted as regex); you can avoid this warning by specifying engine='python'.
  solutions = pd.read_csv(solution_file,sep=', ')


Number of solutions found with SCIP: 120


In [118]:
len(lop_card2.solutions)

120

In [112]:
D3 = addmossimple(D,5,9)
D3

0   1   2   3   4   5   6   7   8   9   10  11  12  13  14  15  16  17  \
0    0   1   1   1   1   1   1   1   1   1   1   1   1   1   1   1   1   1   
1    0   0   1   1   1   1   1   1   1   1   1   1   1   1   1   1   1   1   
2    0   0   0   1   1   1   1   1   1   1   1   1   1   1   1   1   1   1   
3    0   0   0   0   1   1   1   1   1   1   1   1   1   1   1   1   1   1   
4    0   0   0   0   0   1   1   1   1   1   1   1   1   1   1   1   1   1   
5    0   0   0   0   0   0   1   1   1   1   1   1   1   1   1   1   1   1   
6    0   0   0   0   0   1   0   1   1   1   1   1   1   1   1   1   1   1   
7    0   0   0   0   0   1   1   0   1   1   1   1   1   1   1   1   1   1   
8    0   0   0   0   0   1   1   1   0   1   1   1   1   1   1   1   1   1   
9    0   0   0   0   0   1   1   1   1   0   1   1   1   1   1   1   1   1   
10   0   0   0   0   0   0   0   0   0   0   0   1   1   1   1   1   1   1   
11   0   0   0   0   0   0   0   0   0   0   0   0   1   1   1   1   1   1   
12   0   0   0   0   0   0   0   0   0   0   0   0   0   1   1   1   1   1   
13   0   0   0   0   0   0   0   0   0   0   0   0   0   0   1   1   1   1   
14   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   1   1   1   
15   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   1   1   
16   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   1   
17   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   
18   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   
19   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   

    18  19  
0    1   1  
1    1   1  
2    1   1  
3    1   1  
4    1   1  
5    1   1  
6    1   1  
7    1   1  
8    1   1  
9    1   1  
10   1   1  
11   1   1  
12   1   1  
13   1   1  
14   1   1  
15   1   1  
16   1   1  
17   1   1  
18   0   1  
19   0   0

In [115]:
lop_card3 = pyrplib.card.LOP().prepare(pyrplib.transformers.process_D(D3))
lop_card3.run()

Found multiple solutions


/home/jupyter-pander14/ranking_toolbox/pyrankability/search.py:740: ParserWarning: Falling back to the 'python' engine because the 'c' engine does not support regex separators (separators > 1 char and different from '\s+' are interpreted as regex); you can avoid this warning by specifying engine='python'.
  solutions = pd.read_csv(solution_file,sep=', ')


Number of solutions found with SCIP: 120


In [116]:
len(lop_card3.solutions)

120

In [119]:
D4 = addmossimple(D,10,14)
D4

0   1   2   3   4   5   6   7   8   9   10  11  12  13  14  15  16  17  \
0    0   1   1   1   1   1   1   1   1   1   1   1   1   1   1   1   1   1   
1    0   0   1   1   1   1   1   1   1   1   1   1   1   1   1   1   1   1   
2    0   0   0   1   1   1   1   1   1   1   1   1   1   1   1   1   1   1   
3    0   0   0   0   1   1   1   1   1   1   1   1   1   1   1   1   1   1   
4    0   0   0   0   0   1   1   1   1   1   1   1   1   1   1   1   1   1   
5    0   0   0   0   0   0   1   1   1   1   1   1   1   1   1   1   1   1   
6    0   0   0   0   0   0   0   1   1   1   1   1   1   1   1   1   1   1   
7    0   0   0   0   0   0   0   0   1   1   1   1   1   1   1   1   1   1   
8    0   0   0   0   0   0   0   0   0   1   1   1   1   1   1   1   1   1   
9    0   0   0   0   0   0   0   0   0   0   1   1   1   1   1   1   1   1   
10   0   0   0   0   0   0   0   0   0   0   0   1   1   1   1   1   1   1   
11   0   0   0   0   0   0   0   0   0   0   1   0   1   1   1   1   1   1   
12   0   0   0   0   0   0   0   0   0   0   1   1   0   1   1   1   1   1   
13   0   0   0   0   0   0   0   0   0   0   1   1   1   0   1   1   1   1   
14   0   0   0   0   0   0   0   0   0   0   1   1   1   1   0   1   1   1   
15   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   1   1   
16   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   1   
17   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   
18   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   
19   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   

    18  19  
0    1   1  
1    1   1  
2    1   1  
3    1   1  
4    1   1  
5    1   1  
6    1   1  
7    1   1  
8    1   1  
9    1   1  
10   1   1  
11   1   1  
12   1   1  
13   1   1  
14   1   1  
15   1   1  
16   1   1  
17   1   1  
18   0   1  
19   0   0

In [120]:
lop_card4 = pyrplib.card.LOP().prepare(pyrplib.transformers.process_D(D4))
lop_card4.run()

Found multiple solutions


/home/jupyter-pander14/ranking_toolbox/pyrankability/search.py:740: ParserWarning: Falling back to the 'python' engine because the 'c' engine does not support regex separators (separators > 1 char and different from '\s+' are interpreted as regex); you can avoid this warning by specifying engine='python'.
  solutions = pd.read_csv(solution_file,sep=', ')


Number of solutions found with SCIP: 120


In [121]:
len(lop_card4.solutions)

120

In [176]:
pyrankability.plot.show_single_xstar?

Signature:
pyrankability.plot.show_single_xstar(
    x,
    indices=None,
    fixed_r=None,
    width=400,
    height=400,
    labelFontSize=10,
    titleFontSize=10,
    prepare_url_func=None,
    red_green=True,
)
Docstring: <no docstring>
File:      ~/ranking_toolbox/pyrankability/plot.py
Type:      function


In [122]:
D5 = addmossimple(D,15,19)
D5

0   1   2   3   4   5   6   7   8   9   10  11  12  13  14  15  16  17  \
0    0   1   1   1   1   1   1   1   1   1   1   1   1   1   1   1   1   1   
1    0   0   1   1   1   1   1   1   1   1   1   1   1   1   1   1   1   1   
2    0   0   0   1   1   1   1   1   1   1   1   1   1   1   1   1   1   1   
3    0   0   0   0   1   1   1   1   1   1   1   1   1   1   1   1   1   1   
4    0   0   0   0   0   1   1   1   1   1   1   1   1   1   1   1   1   1   
5    0   0   0   0   0   0   1   1   1   1   1   1   1   1   1   1   1   1   
6    0   0   0   0   0   0   0   1   1   1   1   1   1   1   1   1   1   1   
7    0   0   0   0   0   0   0   0   1   1   1   1   1   1   1   1   1   1   
8    0   0   0   0   0   0   0   0   0   1   1   1   1   1   1   1   1   1   
9    0   0   0   0   0   0   0   0   0   0   1   1   1   1   1   1   1   1   
10   0   0   0   0   0   0   0   0   0   0   0   1   1   1   1   1   1   1   
11   0   0   0   0   0   0   0   0   0   0   0   0   1   1   1   1   1   1   
12   0   0   0   0   0   0   0   0   0   0   0   0   0   1   1   1   1   1   
13   0   0   0   0   0   0   0   0   0   0   0   0   0   0   1   1   1   1   
14   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   1   1   1   
15   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   1   1   
16   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   1   0   1   
17   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   1   1   0   
18   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   1   1   1   
19   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   1   1   1   

    18  19  
0    1   1  
1    1   1  
2    1   1  
3    1   1  
4    1   1  
5    1   1  
6    1   1  
7    1   1  
8    1   1  
9    1   1  
10   1   1  
11   1   1  
12   1   1  
13   1   1  
14   1   1  
15   1   1  
16   1   1  
17   1   1  
18   0   1  
19   1   0

In [123]:
lop_card5 = pyrplib.card.LOP().prepare(pyrplib.transformers.process_D(D5))
lop_card5.run()

Found multiple solutions


/home/jupyter-pander14/ranking_toolbox/pyrankability/search.py:740: ParserWarning: Falling back to the 'python' engine because the 'c' engine does not support regex separators (separators > 1 char and different from '\s+' are interpreted as regex); you can avoid this warning by specifying engine='python'.
  solutions = pd.read_csv(solution_file,sep=', ')


Number of solutions found with SCIP: 120


In [124]:
len(lop_card5.solutions)

120

In [216]:
manual_dataset = pyrplib.artificial.create_dataset_manual([D,D2,D3,D4,D5],
                                         {
                                             "start_index":[None,0,5,10,15],
                                             "end_index":[None,4,9,14,19]
                                         },
                                         create_code='addmossimple(D_matrics[0],start_index[i],start_index[i])]')

In [217]:
dataset.to_json("manual_dataset.json")

In [131]:
pd.DataFrame({"beta":[lop_card.beta,lop_card2.beta,lop_card3.beta,lop_card4.beta,lop_card5.beta],
              "tau":[lop_card.tau_farthest_pair,lop_card2.tau_farthest_pair,lop_card3.tau_farthest_pair,lop_card4.tau_farthest_pair,lop_card5.tau_farthest_pair],
              "obj":[lop_card.obj,lop_card2.obj,lop_card3.obj,lop_card4.obj,lop_card5.obj],
              "nmos":[len(lop_card.solutions),len(lop_card2.solutions),len(lop_card3.solutions),len(lop_card4.solutions),len(lop_card5.solutions)]
             })

beta       tau    obj  nmos
0  0.000000       NaN  190.0     1
1  0.000088  0.894737  190.0   120
2  0.000024  0.894737  190.0   120
3  0.000014  0.894737  190.0   120
4  0.000010  0.894737  190.0   120

In [132]:
processed_datasets_df = rplib_data.processed_datasets_df.set_index('Dataset ID')

In [192]:
mm_2002_dataset_direct = processed_datasets_df.loc[1]
mm_2002_dataset_indirect = processed_datasets_df.loc[2]
D_direct = pyrplib.dataset.ProcessedD.from_json(mm_2002_dataset_direct['Link']).load().data
D_indirect = pyrplib.dataset.ProcessedD.from_json(mm_2002_dataset_indirect['Link']).load().data
D_2002 = D_direct.fillna(0) + D_indirect.fillna(0)

In [ ]:
lop_card_2002 = pyrplib.card.LOP().prepare(pyrplib.transformers.process_D(D_2002)).run()

Found multiple solutions


In [205]:
visuals = lop_card_2002.get_visuals()['notebook']
for key in visuals:
    display(Markdown(f"### {key}"))
    display(visuals[key])

### D[r,r]

Kansas  Oklahoma  Arizona  Duke  Gonzaga  Hawaii  Texas_Tech  \
Kansas          0.0       0.0      1.0   1.0      0.0     0.0         0.0   
Oklahoma        3.0       0.0      0.0   0.0      0.0     0.0         2.0   
Arizona         1.0       1.0      0.0   0.0      0.0     0.0         0.0   
Duke            0.0       1.0      1.0   0.0      0.0     0.0         0.0   
Gonzaga         0.0       0.0      2.0   0.0      0.0     0.0         0.0   
...             ...       ...      ...   ...      ...     ...         ...   
IL_Chicago      0.0       0.0      1.0   0.0      0.0     0.0         0.0   
Boston_Univ     0.0       0.0      0.0   2.0      0.0     0.0         0.0   
Murray_St       0.0       1.0      0.0   0.0      0.0     0.0         0.0   
Holy_Cross      1.0       0.0      0.0   2.0      0.0     1.0         0.0   
Alcorn_St       0.0       0.0      0.0   0.0      1.0     3.0         2.0   

             Oklahoma_St  Connecticut  Oregon  ...  Hampton  Davidson  Siena  \
Kansas               1.0          0.0     2.0  ...      0.0       0.0    0.0   
Oklahoma             2.0          0.0     0.0  ...      0.0       0.0    0.0   
Arizona              0.0          1.0     8.0  ...      0.0       0.0    0.0   
Duke                 0.0          0.0     0.0  ...      0.0       0.0    0.0   
Gonzaga              0.0          0.0     1.0  ...      0.0       0.0    0.0   
...                  ...          ...     ...  ...      ...       ...    ...   
IL_Chicago           0.0          0.0     0.0  ...      1.0       0.0    0.0   
Boston_Univ          1.0          5.0     0.0  ...      0.0       0.0    1.0   
Murray_St            1.0          0.0     1.0  ...      0.0       1.0    1.0   
Holy_Cross           0.0          4.0     0.0  ...      0.0       0.0    2.0   
Alcorn_St            0.0          0.0     2.0  ...      0.0       0.0    0.0   

             W_Kentucky  FL_Atlantic  IL_Chicago  Boston_Univ  Murray_St  \
Kansas              1.0          0.0         0.0          0.0        0.0   
Oklahoma            0.0          0.0         0.0          0.0        0.0   
Arizona             0.0          0.0         0.0          0.0        0.0   
Duke                0.0          0.0         0.0          0.0        0.0   
Gonzaga             0.0          0.0         0.0          0.0        0.0   
...                 ...          ...         ...          ...        ...   
IL_Chicago          2.0          0.0         0.0          0.0        0.0   
Boston_Univ         0.0          0.0         0.0          0.0        0.0   
Murray_St           0.0          0.0         1.0          0.0        0.0   
Holy_Cross          0.0          0.0         0.0          2.0        0.0   
Alcorn_St           1.0          0.0         0.0          0.0        1.0   

             Holy_Cross  Alcorn_St  
Kansas              0.0        0.0  
Oklahoma            0.0        0.0  
Arizona             0.0        0.0  
Duke                0.0        0.0  
Gonzaga             0.0        0.0  
...                 ...        ...  
IL_Chicago          0.0        0.0  
Boston_Univ         0.0        0.0  
Murray_St           0.0        0.0  
Holy_Cross          0.0        0.0  
Alcorn_St           0.0        0.0  

[65 rows x 65 columns]

### Red/Green plot

alt.Chart(...)

### X*

...

0.8471153846153846

### TAU Closest Pair

0.9990384615384615

### Number of optimal solutions found

1054

In [200]:
mm_2008_dataset_direct = processed_datasets_df.loc[13]
mm_2008_dataset_indirect = processed_datasets_df.loc[14]
D_direct = pyrplib.dataset.ProcessedD.from_json(mm_2008_dataset_direct['Link']).load().data
D_indirect = pyrplib.dataset.ProcessedD.from_json(mm_2008_dataset_indirect['Link']).load().data
D_2008 = D_direct.fillna(0) + D_indirect.fillna(0)

In [201]:
lop_card_2008 = pyrplib.card.LOP().prepare(pyrplib.transformers.process_D(D_2008)).run()

Found multiple solutions


/home/jupyter-pander14/ranking_toolbox/pyrankability/search.py:740: ParserWarning: Falling back to the 'python' engine because the 'c' engine does not support regex separators (separators > 1 char and different from '\s+' are interpreted as regex); you can avoid this warning by specifying engine='python'.
  solutions = pd.read_csv(solution_file,sep=', ')


Number of solutions found with SCIP: 1015


In [206]:
visuals = lop_card_2008.get_visuals()['notebook']
for key in visuals:
    display(Markdown(f"### {key}"))
    display(visuals[key])

### D[r,r]

North_Carolina  Duke  Butler  Kansas  Wisconsin  Texas  \
North_Carolina             0.0   3.0     0.0     0.0        0.0    0.0   
Duke                       3.0   0.0     0.0     0.0        0.0    0.0   
Butler                     0.0   0.0     0.0     0.0        0.0    0.0   
Kansas                     0.0   0.0     0.0     0.0        1.0    4.0   
Wisconsin                  1.0   2.0     0.0     0.0        0.0    0.0   
...                        ...   ...     ...     ...        ...    ...   
Mt_St_Mary's               0.0   0.0     0.0     1.0        0.0    2.0   
Coppin_St                  2.0   2.0     1.0     2.0        4.0    0.0   
Winthrop                   3.0   1.0     0.0     1.0        0.0    2.0   
MS_Valley_St               0.0   0.0     0.0     2.0        0.0    2.0   
Austin_Peay                1.0   0.0     3.0     0.0        1.0    0.0   

                Tennessee  Memphis  Clemson  UCLA  ...  UMBC  Oregon  \
North_Carolina        0.0      0.0      1.0   1.0  ...   0.0     0.0   
Duke                  0.0      0.0      2.0   0.0  ...   0.0     0.0   
Butler                0.0      0.0      0.0   0.0  ...   0.0     0.0   
Kansas                0.0      0.0      0.0   0.0  ...   0.0     1.0   
Wisconsin             0.0      0.0      2.0   0.0  ...   0.0     0.0   
...                   ...      ...      ...   ...  ...   ...     ...   
Mt_St_Mary's          0.0      1.0      0.0   3.0  ...   3.0     1.0   
Coppin_St             3.0      0.0      0.0   2.0  ...   3.0     1.0   
Winthrop              4.0      1.0      0.0   1.0  ...   0.0     1.0   
MS_Valley_St          2.0      2.0      0.0   2.0  ...   0.0     0.0   
Austin_Peay           2.0      1.0      1.0   0.0  ...   0.0     0.0   

                St_Joseph's_PA  CS_Fullerton  Portland_St  Mt_St_Mary's  \
North_Carolina             0.0           0.0          0.0           0.0   
Duke                       0.0           0.0          0.0           0.0   
Butler                     0.0           0.0          0.0           0.0   
Kansas                     0.0           0.0          0.0           0.0   
Wisconsin                  0.0           0.0          0.0           0.0   
...                        ...           ...          ...           ...   
Mt_St_Mary's               2.0           0.0          0.0           0.0   
Coppin_St                  1.0           0.0          0.0           0.0   
Winthrop                   0.0           0.0          0.0           1.0   
MS_Valley_St               0.0           2.0          4.0           0.0   
Austin_Peay                0.0           0.0          1.0           0.0   

                Coppin_St  Winthrop  MS_Valley_St  Austin_Peay  
North_Carolina        0.0       0.0           0.0          0.0  
Duke                  0.0       1.0           0.0          0.0  
Butler                0.0       0.0           0.0          0.0  
Kansas                0.0       0.0           0.0          0.0  
Wisconsin             0.0       0.0           0.0          0.0  
...                   ...       ...           ...          ...  
Mt_St_Mary's          0.0       0.0           0.0          0.0  
Coppin_St             0.0       0.0           0.0          0.0  
Winthrop              0.0       0.0           0.0          0.0  
MS_Valley_St          0.0       0.0           0.0          0.0  
Austin_Peay           1.0       1.0           0.0          0.0  

[64 rows x 64 columns]

### Red/Green plot

alt.Chart(...)

### X*

...

0.8849206349206349

### TAU Closest Pair

0.9990079365079365

### Number of optimal solutions found

1023

In [ ]:
lop_card_mm_2002 = pyrplib.card.LOP().prepare(mm_2002_dataset)
lop_card_mm_2002.run()

Found multiple solutions


/home/jupyter-pander14/ranking_toolbox/pyrankability/search.py:740: ParserWarning: Falling back to the 'python' engine because the 'c' engine does not support regex separators (separators > 1 char and different from '\s+' are interpreted as regex); you can avoid this warning by specifying engine='python'.
  solutions = pd.read_csv(solution_file,sep=', ')


Number of solutions found with SCIP: 1011


In [138]:
len(lop_card_mm_2002.solutions)

1019

## MM 2002

In [170]:
lop_card_mm_2002.D.index[np.array(lop_card_mm_2002.outlier_solution)]

Index(['San_Diego_St', 'Pepperdine', 'Utah', 'Wyoming', 'Santa_Barbara',
       'Wake_Forest', 'Stanford', 'USC', 'California', 'Central_Conn',
       'McNeese_St', 'Siena', 'Creighton', 'W_Kentucky', 'Kent', 'Xavier',
       'IL_Chicago', 'Mississippi_St', 'Penn', 'Davidson', 'Charlotte',
       'Cincinnati', 'Oklahoma_St', 'Missouri', 'Texas_Tech', 'Texas',
       'Valparaiso', 'Florida', 'Mississippi', 'Indiana', 'Murray_St',
       'S_Illinois', 'FL_Atlantic', 'Miami_FL', 'Holy_Cross', 'Boston_Univ',
       'Boston_College', 'St_John's', 'Montana', 'Gonzaga', 'Illinois',
       'Arizona', 'Connecticut', 'NC_State', 'Maryland', 'Oklahoma', 'Tulsa',
       'Kansas', 'UNC_Wilmington', 'Ohio_St', 'Pittsburgh', 'Notre_Dame',
       'Kentucky', 'Georgia', 'Alabama', 'UCLA', 'Oregon', 'Wisconsin', 'Duke',
       'Marquette', 'Michigan_St', 'Winthrop', 'Alcorn_St', 'Hawaii'],
      dtype='object')

In [178]:
visuals = lop_card_mm_2002.get_visuals()['notebook']
for key in visuals:
    display(Markdown(f"### {key}"))
    display(visuals[key])
#lop_card_mm_2002.get_visuals()['notebook']['Red/Green plot']

### D[r,r]

Oregon  UCLA  Kansas  Arizona  Oklahoma  Duke  Alabama  Hawaii  \
Oregon         0.0   0.0     0.0      0.0       0.0   0.0      0.0     0.0   
UCLA           2.0   0.0     0.0      1.0       0.0   0.0      0.0     0.0   
Kansas         0.0   1.0     0.0      0.0       0.0   0.0      0.0     0.0   
Arizona        2.0   1.0     1.0      0.0       0.0   0.0      0.0     0.0   
Oklahoma       0.0   0.0     1.0      0.0       0.0   0.0      0.0     0.0   
...            ...   ...     ...      ...       ...   ...      ...     ...   
NC_State       0.0   0.0     0.0      0.0       0.0   2.0      0.0     0.0   
Charlotte      0.0   0.0     0.0      0.0       0.0   0.0      0.0     0.0   
W_Kentucky     1.0   0.0     0.0      0.0       0.0   0.0      0.0     0.0   
Davidson       0.0   0.0     0.0      0.0       0.0   1.0      0.0     0.0   
Penn           0.0   0.0     0.0      0.0       0.0   0.0      0.0     0.0   

            Wisconsin  Maryland  ...  Siena  UNC_Wilmington  Holy_Cross  \
Oregon            0.0       0.0  ...    0.0             0.0         0.0   
UCLA              0.0       0.0  ...    0.0             0.0         0.0   
Kansas            0.0       0.0  ...    0.0             0.0         0.0   
Arizona           0.0       0.0  ...    0.0             0.0         0.0   
Oklahoma          0.0       0.0  ...    0.0             0.0         0.0   
...               ...       ...  ...    ...             ...         ...   
NC_State          0.0       2.0  ...    0.0             0.0         0.0   
Charlotte         0.0       0.0  ...    0.0             0.0         0.0   
W_Kentucky        0.0       0.0  ...    0.0             0.0         0.0   
Davidson          0.0       0.0  ...    0.0             0.0         0.0   
Penn              0.0       0.0  ...    0.0             0.0         0.0   

            FL_Atlantic  IL_Chicago  NC_State  Charlotte  W_Kentucky  \
Oregon              0.0         0.0       0.0        0.0         0.0   
UCLA                0.0         0.0       0.0        0.0         0.0   
Kansas              0.0         0.0       0.0        0.0         0.0   
Arizona             0.0         0.0       0.0        0.0         0.0   
Oklahoma            0.0         0.0       0.0        0.0         0.0   
...                 ...         ...       ...        ...         ...   
NC_State            0.0         0.0       0.0        0.0         0.0   
Charlotte           0.0         0.0       0.0        0.0         0.0   
W_Kentucky          0.0         0.0       0.0        0.0         0.0   
Davidson            0.0         0.0       0.0        1.0         0.0   
Penn                0.0         0.0       0.0        0.0         0.0   

            Davidson  Penn  
Oregon           0.0   0.0  
UCLA             0.0   0.0  
Kansas           0.0   0.0  
Arizona          0.0   0.0  
Oklahoma         0.0   0.0  
...              ...   ...  
NC_State         0.0   0.0  
Charlotte        0.0   0.0  
W_Kentucky       0.0   0.0  
Davidson         0.0   0.0  
Penn             1.0   0.0  

[64 rows x 64 columns]

### Red/Green plot

alt.Chart(...)

### X*

alt.Chart(...)

### Nearest and Farthest

alt.LayerChart(...)

### Farthest Pair

alt.LayerChart(...)

In [ ]:
lop_card_mm_2008 = pyrplib.card.LOP().prepare(mm_2008_dataset)
lop_card_mm_2008.run()

Found multiple solutions


In [175]:
visuals = lop_card_mm_2008.get_visuals()['notebook']
for key in visuals:
    display(Markdown(f"### {key}"))
    display(visuals[key])

### D[r,r]

Duke  North_Carolina  Clemson  Purdue  Wisconsin  UCLA  Texas  \
Duke             0.0             1.0      0.0     0.0        0.0   0.0    0.0   
North_Carolina   1.0             0.0      0.0     0.0        0.0   0.0    0.0   
Clemson          1.0             2.0      0.0     0.0        0.0   0.0    0.0   
Purdue           0.0             0.0      1.0     0.0        0.0   0.0    0.0   
Wisconsin        1.0             0.0      0.0     2.0        0.0   0.0    0.0   
...              ...             ...      ...     ...        ...   ...    ...   
Butler           0.0             0.0      0.0     0.0        0.0   0.0    0.0   
Mississippi_St   0.0             0.0      1.0     0.0        0.0   0.0    0.0   
Kentucky         0.0             1.0      0.0     0.0        0.0   0.0    0.0   
Oral_Roberts     0.0             0.0      0.0     0.0        0.0   0.0    1.0   
Georgia          0.0             0.0      0.0     0.0        1.0   0.0    0.0   

                Tennessee  Cornell  Stanford  ...  Winthrop  Coppin_St  \
Duke                  0.0      0.0       0.0  ...       0.0        0.0   
North_Carolina        0.0      0.0       0.0  ...       0.0        0.0   
Clemson               0.0      0.0       0.0  ...       0.0        0.0   
Purdue                0.0      0.0       0.0  ...       0.0        0.0   
Wisconsin             0.0      0.0       0.0  ...       0.0        0.0   
...                   ...      ...       ...  ...       ...        ...   
Butler                0.0      0.0       0.0  ...       0.0        0.0   
Mississippi_St        1.0      0.0       0.0  ...       0.0        0.0   
Kentucky              1.0      0.0       0.0  ...       0.0        0.0   
Oral_Roberts          0.0      0.0       0.0  ...       0.0        0.0   
Georgia               2.0      0.0       0.0  ...       0.0        0.0   

                Miami_FL  Portland_St  Texas_A&M  Butler  Mississippi_St  \
Duke                 1.0          0.0        0.0     0.0             0.0   
North_Carolina       0.0          0.0        0.0     0.0             0.0   
Clemson              1.0          0.0        0.0     0.0             0.0   
Purdue               0.0          0.0        0.0     0.0             0.0   
Wisconsin            0.0          0.0        0.0     0.0             0.0   
...                  ...          ...        ...     ...             ...   
Butler               0.0          0.0        0.0     0.0             0.0   
Mississippi_St       1.0          0.0        0.0     0.0             0.0   
Kentucky             0.0          0.0        0.0     0.0             1.0   
Oral_Roberts         0.0          0.0        1.0     0.0             0.0   
Georgia              0.0          0.0        0.0     0.0             1.0   

                Kentucky  Oral_Roberts  Georgia  
Duke                 0.0           0.0      0.0  
North_Carolina       0.0           0.0      0.0  
Clemson              0.0           0.0      0.0  
Purdue               0.0           0.0      0.0  
Wisconsin            0.0           0.0      0.0  
...                  ...           ...      ...  
Butler               0.0           0.0      0.0  
Mississippi_St       0.0           0.0      0.0  
Kentucky             0.0           0.0      0.0  
Oral_Roberts         0.0           0.0      0.0  
Georgia              2.0           0.0      0.0  

[63 rows x 63 columns]

### Red/Green plot

alt.Chart(...)

### Nearest and Farthest

alt.LayerChart(...)

### Farthest Pair

alt.LayerChart(...)

In [152]:
"%.5f"%lop_card_mm_2002.beta,"%.5f"%lop_card_mm_2008.beta

('0.00018', '0.00005')